In [1]:
import pandas as pd
import numpy as np

/home/lap13607/anaconda3/lib/python3.8/site-packages/pandas/core/computation/expressions.py:20: UserWarning: Pandas requires version '2.7.3' or newer of 'numexpr' (version '2.7.1' currently installed).
  from pandas.core.computation.check import NUMEXPR_INSTALLED


In [2]:
df = pd.read_csv('gena_data_final.csv')
df.head(5)

PMID                                           Sentence      ID_1   
0  31196764  Flibanserin, a multifunctional serotonin recep...   C098107  \
1  31196764  Flibanserin, a multifunctional serotonin recep...   C098107   
2  31196764  Flibanserin, a multifunctional serotonin recep...  NEW00001   
3  31196764  Flibanserin, a multifunctional serotonin recep...  NEW00001   
4  27584019  Obesity is associated with reduced testosteron...   D063766   

                                           E1   Type_E1   
0                                 Flibanserin  CHEMICAL  \
1                                 Flibanserin  CHEMICAL   
2  multifunctional serotonin receptor agonist  CHEMICAL   
3  multifunctional serotonin receptor agonist  CHEMICAL   
4                                     Obesity   DISEASE   

                                      Full_E1   
0                                 Flibanserin  \
1                                 Flibanserin   
2  multifunctional serotonin receptor agonist   
3  multifunctional serotonin receptor agonist   
4                                     Obesity   

                                      MeSH_E1   
0         flibanserin [Supplementary Concept]  \
1         flibanserin [Supplementary Concept]   
2  multifunctional serotonin receptor agonist   
3  multifunctional serotonin receptor agonist   
4                           Pediatric Obesity   

                                          Synonyms_1   
0                                     Benzimidazoles  \
1                                     Benzimidazoles   
2                                        No synonyms   
3                                        No synonyms   
4  Obesity, Pediatric|Obesity in Childhood|Childh...   

                                            Relation      ID_2   
0  be approved in united states and canada for tr...  NEW00000  \
1  be approved in united states and canada for tr...   D020018   
2  be approved in united states and canada for tr...  NEW00000   
3  be approved in united states and canada for tr...   D020018   
4                                 be associated with  NEW00002   

                                                  E2        Type_E2   
0  acquired generalized hypoactive sexual desire ...  MENTAL_HEALTH  \
1                                               HSDD        DISEASE   
2  acquired generalized hypoactive sexual desire ...  MENTAL_HEALTH   
3                                               HSDD        DISEASE   
4                               reduced testosterone       CHEMICAL   

                                             Full_E2   
0  acquired generalized hypoactive sexual desire ...  \
1                  hypoactive sexual desire disorder   
2  acquired generalized hypoactive sexual desire ...   
3                  hypoactive sexual desire disorder   
4                               reduced testosterone   

                                             MeSH_E2   
0  acquired generalized hypoactive sexual desire ...  \
1                 Sexual Dysfunctions, Psychological   
2  acquired generalized hypoactive sexual desire ...   
3                 Sexual Dysfunctions, Psychological   
4                               reduced testosterone   

                                          Synonyms_2  
0                                        No synonyms  
1  Dysfunction, Psychological Sexual|Dysfunctions...  
2                                        No synonyms  
3  Dysfunction, Psychological Sexual|Dysfunctions...  
4                                        No synonyms

In [1]:
from neo4j import GraphDatabase
from neo4j.exceptions import ServiceUnavailable
import pandas as pd
import itertools
import os
from time import sleep
import re
from pandas.core.frame import DataFrame


/home/lap13607/anaconda3/lib/python3.8/site-packages/pandas/core/computation/expressions.py:20: UserWarning: Pandas requires version '2.7.3' or newer of 'numexpr' (version '2.7.1' currently installed).
  from pandas.core.computation.check import NUMEXPR_INSTALLED


In [5]:
class Gena:
    def __init__(self, uri, user, password):
        self.driver = GraphDatabase.driver(uri, auth=(user, password))

    def close(self):
        # Don't forget to close the driver connection when you are finished with it
        self.driver.close()
    
    def create_nodes(self, node_df):
        with self.driver.session() as session:
            create_nodes_query = "CREATE "
            nodes = []
            for idx, row in node_df.iterrows():
                unique_id = row['ID']
                name = row['Preferred label'].replace('"', '')
                label = row['Label'].upper()
                synonyms = row['Synonyms'].replace('"', '')
                nodes.append("(n" + str(idx) + ":" + label + " {id: " + f'"{unique_id}"' + ", name: " + f'"{name}"' + ", synonyms:" + f'"{synonyms}"' + "})")
        
#         with open("test_nodes.txt", "w", encoding="utf-8") as f:
#             print("write query to file.")
#             f.write(create_nodes_query + ",".join(nodes))
            session.run(create_nodes_query + ",".join(nodes))
                
    def create_relationships(self, relation_df):
        with self.driver.session() as session:
            for idx, row in relation_df.iterrows():
                id_1 = row['ID_1']
                label_1 = row['Type_E1'].upper()
                id_2 = row['ID_2']
                label_2 = row['Type_E2'].upper()
                relation = re.sub('[^A-Za-z0-9|_]+', '', row['Relation'].upper().replace(' ', '_'))

                had_relation = [result for result in session.run("MATCH p = (node_1)-[r:`CID`]->(node_2) WHERE (node_1.id = $id_1 AND node_2.id = $id_2) RETURN nodes(p)", id_1=id_1, id_2=id_2)]
                if len(had_relation) > 0:
                    try:
                        pmid_source = str(int(row['PMID']))
                        create_relation = f'MATCH (node_1)-[r:CID]->(node_2)\
                        \nWHERE (node_1.id = "{id_1}" AND node_2.id = "{id_2}")\
                        \nSET r.detail = (CASE r.detail WHEN null THEN ["{relation}"] ELSE r.detail + ["{relation}"] END), r.source = r.source + ["{pmid_source}"]'
                        
                        display(create_relation)
                        session.run(create_relation)
                    except Exception as e:
                        print(idx)
                        print(e)
                        print('---')
                else:
                    create_relation = f'MATCH (node_1), (node_2) WHERE (node_1.id = "{id_1}" AND node_2.id = "{id_2}") MERGE (node_1)-[r:`{relation}`' + ' {source:["' + row["PMID"] + '"]}]->(node_2)'
                    display(create_relation)
                    session.run(create_relation)

    def delete_data(self):
        with self.driver.session() as session:
            session.run("MATCH (n) DETACH DELETE n")

In [9]:
## Call GENA
uri = "neo4j+s://e5c905b4.databases.neo4j.io"
user = "neo4j"
password = "jpAl3O0n2X4Znvco3LtqM9fGoNamvGJH4PpdxPEJvlM"
gena = Gena(uri, user, password)

In [6]:
import time
nodes_df = pd.read_csv(f"ID_to_ENTITIES_final.csv")
pre_count = 0
count = 2000

while True:
    print(f"Create nodes from {pre_count} to {count}")
    gena.create_nodes(nodes_df[pre_count:count])
    if count > len(nodes_df):
        break
    pre_count = count
    count += 2000


Create nodes from 0 to 2000
Create nodes from 2000 to 4000
Create nodes from 4000 to 6000
Create nodes from 6000 to 8000
Create nodes from 8000 to 10000
Create nodes from 10000 to 12000
Create nodes from 12000 to 14000
Create nodes from 14000 to 16000
Create nodes from 16000 to 18000
Create nodes from 18000 to 20000
Create nodes from 20000 to 22000
Create nodes from 22000 to 24000
Create nodes from 24000 to 26000
Create nodes from 26000 to 28000
Create nodes from 28000 to 30000


In [11]:
## Create Relationship
relationships = pd.read_csv(f"gena_data_final.csv")
pre_count = 20000
count = 24000
reverse_relation = relationships[::-1].reset_index(drop=True)
while True:
    print(f"Create relationship from {pre_count} to {count}")
    gena.create_relationships(reverse_relation[pre_count:count])
    if count > len(reverse_relation):
        break
    pre_count = count
    count += 4000
    sleep(5)

Create relationship from 20000 to 24000


'MATCH (node_1), (node_2) WHERE (node_1.id = "D019422" AND node_2.id = "D065626") MERGE (node_1)-[r:`DRIVING_FORCE_BEHIND` {source:["23793849"]}]->(node_2)'

'MATCH (node_1), (node_2) WHERE (node_1.id = "D019422" AND node_2.id = "D054586") MERGE (node_1)-[r:`DRIVING_FORCE_BEHIND` {source:["23793849"]}]->(node_2)'

'MATCH (node_1), (node_2) WHERE (node_1.id = "D006397" AND node_2.id = "D054144") MERGE (node_1)-[r:`IMPROVE_EXERCISE_CAPACITY_IN_ANAEMIC_PATIENTS_WITH` {source:["32392403"]}]->(node_2)'

'MATCH (node_1), (node_2) WHERE (node_1.id = "D018763" AND node_2.id = "D012080") MERGE (node_1)-[r:`IN_PATIENTS_WITH` {source:["33858827"]}]->(node_2)'

...

'MATCH (node_1), (node_2) WHERE (node_1.id = "D063766" AND node_2.id = "NEW00002") MERGE (node_1)-[r:`BE_ASSOCIATED_WITH` {source:["27584019"]}]->(node_2)'

'MATCH (node_1), (node_2) WHERE (node_1.id = "NEW00001" AND node_2.id = "D020018") MERGE (node_1)-[r:`BE_APPROVED_IN_UNITED_STATES_AND_CANADA_FOR_TREATMENT_OF` {source:["31196764"]}]->(node_2)'

'MATCH (node_1), (node_2) WHERE (node_1.id = "NEW00001" AND node_2.id = "NEW00000") MERGE (node_1)-[r:`BE_APPROVED_IN_UNITED_STATES_AND_CANADA_FOR_TREATMENT_OF` {source:["31196764"]}]->(node_2)'

'MATCH (node_1), (node_2) WHERE (node_1.id = "C098107" AND node_2.id = "D020018") MERGE (node_1)-[r:`BE_APPROVED_IN_UNITED_STATES_AND_CANADA_FOR_TREATMENT_OF` {source:["31196764"]}]->(node_2)'

'MATCH (node_1), (node_2) WHERE (node_1.id = "C098107" AND node_2.id = "NEW00000") MERGE (node_1)-[r:`BE_APPROVED_IN_UNITED_STATES_AND_CANADA_FOR_TREATMENT_OF` {source:["31196764"]}]->(node_2)'

In [12]:
cid_relation = reverse_relation.iloc[[10215, 10417, 17413, 24874, 28331, 29734, 30433, 30749, 30981, 31776, 32015, 33512, 33718, 35366, 35808,
                      38663, 38967, 40255, 41356, 41922, 42688], :]
gena.create_relationships(cid_relation)

'MATCH (node_1)-[r:CID]->(node_2)                        \nWHERE (node_1.id = "D003024" AND node_2.id = "D020820")                        \nSET r.detail = (CASE r.detail WHEN null THEN ["SHOW_EFFICACY_AS_TREATMENT_FOR"] ELSE r.detail + ["SHOW_EFFICACY_AS_TREATMENT_FOR"] END), r.source = r.source + ["7856623"]'

'MATCH (node_1), (node_2) WHERE (node_1.id = "C105101" AND node_2.id = "NEW17129") MERGE (node_1)-[r:`CAUSE` {source:["16436471"]}]->(node_2)'

'MATCH (node_1)-[r:CID]->(node_2)                        \nWHERE (node_1.id = "D004837" AND node_2.id = "D006323")                        \nSET r.detail = (CASE r.detail WHEN null THEN ["HAVE_THE_USE_TO"] ELSE r.detail + ["HAVE_THE_USE_TO"] END), r.source = r.source + ["7502643"]'

'MATCH (node_1)-[r:CID]->(node_2)                        \nWHERE (node_1.id = "D007649" AND node_2.id = "D006212")                        \nSET r.detail = (CASE r.detail WHEN null THEN ["INDUCE"] ELSE r.detail + ["INDUCE"] END), r.source = r.source + ["18022604"]'

'MATCH (node_1)-[r:CID]->(node_2)                        \nWHERE (node_1.id = "D018967" AND node_2.id = "D006966")                        \nSET r.detail = (CASE r.detail WHEN null THEN ["BE_RESERVED_GIVEN_POTENTIAL_DEVELOPMENT_OF_ATHEROSCLEROSIS_IN_OBESITY_AND_ENDOCRINE_RESPONSE_IN"] ELSE r.detail + ["BE_RESERVED_GIVEN_POTENTIAL_DEVELOPMENT_OF_ATHEROSCLEROSIS_IN_OBESITY_AND_ENDOCRINE_RESPONSE_IN"] END), r.source = r.source + ["12625994"]'

...

'MATCH (node_1)-[r:CID]->(node_2)                        \nWHERE (node_1.id = "D007649" AND node_2.id = "D006212")                        \nSET r.detail = (CASE r.detail WHEN null THEN ["BE_COMPLICATED_BY"] ELSE r.detail + ["BE_COMPLICATED_BY"] END), r.source = r.source + ["27656531"]'

'MATCH (node_1)-[r:CID]->(node_2)                        \nWHERE (node_1.id = "D007649" AND node_2.id = "D006212")                        \nSET r.detail = (CASE r.detail WHEN null THEN ["CAUSE"] ELSE r.detail + ["CAUSE"] END), r.source = r.source + ["26442907"]'

'MATCH (node_1)-[r:CID]->(node_2)                        \nWHERE (node_1.id = "D003024" AND node_2.id = "D009205")                        \nSET r.detail = (CASE r.detail WHEN null THEN ["BE_EFFECTIVE_MEDICATION_FOR"] ELSE r.detail + ["BE_EFFECTIVE_MEDICATION_FOR"] END), r.source = r.source + ["35067911"]'

'MATCH (node_1)-[r:CID]->(node_2)                        \nWHERE (node_1.id = "D003024" AND node_2.id = "D000380")                        \nSET r.detail = (CASE r.detail WHEN null THEN ["CAUSE_FATAL_HEMATOPOIETIC_TOXICITY_AS"] ELSE r.detail + ["CAUSE_FATAL_HEMATOPOIETIC_TOXICITY_AS"] END), r.source = r.source + ["27368152"]'

'MATCH (node_1)-[r:CID]->(node_2)                        \nWHERE (node_1.id = "D000638" AND node_2.id = "D001919")                        \nSET r.detail = (CASE r.detail WHEN null THEN ["PRODUCE"] ELSE r.detail + ["PRODUCE"] END), r.source = r.source + ["33165142"]'